# OpenTripPlanner Routing Example in Python

This notebook demonstrates routing using OpenTripPlanner (OTP) in Python, replicating the R example.
We'll create a walking route from Institute for Transport Studies, Leeds to Leeds Railway Station.


In [30]:
# # Install required packages
# %pip install requests geopy folium geopandas polyline

In [9]:
import requests
import json
from geopy.geocoders import Nominatim
import folium
import geopandas as gpd
from shapely.geometry import LineString, Point
import pandas as pd
import polyline  # For decoding OTP polylines


## 1. Geocode Locations

First, we'll geocode our origin and destination addresses using geopy.


In [24]:
# Initialize geocoder
geolocator = Nominatim(user_agent="otp_routing_example")

# Geocode the locations
from_location = geolocator.geocode("Institute for Transport Studies, Leeds")
to_location = geolocator.geocode("Leeds Railway Station")

print(f"From: {from_location}")
print(f"  Coordinates: {from_location.latitude}, {from_location.longitude}")
print(f"\nTo: {to_location}")
print(f"  Coordinates: {to_location.latitude}, {to_location.longitude}")


From: Institute for Transport Studies, University Road, Little Woodhouse, Woodhouse, Leeds, West Yorkshire, England, LS2 9JY, United Kingdom
  Coordinates: 53.8080358, -1.5583375

To: Leeds Railway Station, New Station Street, Crown Point, Lovell Park, Leeds, West Yorkshire, England, LS1 1PJ, United Kingdom
  Coordinates: 53.7952356, -1.547738


## 2. Connect to OpenTripPlanner Server

We'll connect to the same OTP server used in the R example.


In [25]:
# OTP server configuration (same as R example)
OTP_BASE_URL = "https://otp.robinlovelace.net/otp/routers/west-yorkshire/plan"

def otp_plan(from_lat, from_lon, to_lat, to_lon, mode="WALK"):
    """
    Plan a route using OpenTripPlanner
    """
    params = {
        'fromPlace': f"{from_lat},{from_lon}",
        'toPlace': f"{to_lat},{to_lon}",
        'mode': mode,
        'maxWalkDistance': 2000,
        'arriveBy': 'false'
    }
    
    try:
        response = requests.get(OTP_BASE_URL, params=params, timeout=30)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        print(f"Error connecting to OTP server: {e}")
        return None

# Test connection
print("Testing connection to OTP server...")
test_response = requests.get("https://otp.robinlovelace.net", timeout=10)
print(f"Connection status: {test_response.status_code}")


Testing connection to OTP server...
Connection status: 200


## 6. Multi-Modal Routing

Now let's explore different transport modes including public transit and cycling.


In [26]:
# Function to plan routes with different modes
def plan_multimodal_routes():
    """Plan routes using different transport modes"""
    routes = {}
    
    # Public transport route (Walk + Transit)
    print("Planning public transport route...")
    routes['transit'] = otp_plan(
        from_lat=from_location.latitude,
        from_lon=from_location.longitude,
        to_lat=to_location.latitude,
        to_lon=to_location.longitude,
        mode="WALK,TRANSIT"
    )
    
    # Cycling with public transport
    print("Planning cycling + transit route...")
    routes['bike_transit'] = otp_plan(
        from_lat=from_location.latitude,
        from_lon=from_location.longitude,
        to_lat=to_location.latitude,
        to_lon=to_location.longitude,
        mode="BICYCLE,TRANSIT"
    )
    
    # Pure cycling route
    print("Planning cycling route...")
    routes['bicycle'] = otp_plan(
        from_lat=from_location.latitude,
        from_lon=from_location.longitude,
        to_lat=to_location.latitude,
        to_lon=to_location.longitude,
        mode="BICYCLE"
    )
    
    # Driving route
    print("Planning driving route...")
    routes['car'] = otp_plan(
        from_lat=from_location.latitude,
        from_lon=from_location.longitude,
        to_lat=to_location.latitude,
        to_lon=to_location.longitude,
        mode="CAR"
    )
    
    return routes

# Plan all routes
multimodal_routes = plan_multimodal_routes()

# Check which routes were successful
for mode, route_data in multimodal_routes.items():
    if route_data and 'plan' in route_data:
        itinerary = route_data['plan']['itineraries'][0]
        duration_min = itinerary['duration'] / 60
        print(f"✓ {mode.upper()}: {duration_min:.1f} minutes")
    else:
        print(f"✗ {mode.upper()}: No route found")


Planning public transport route...
Planning cycling + transit route...
Planning cycling route...
Planning driving route...
✓ TRANSIT: 24.3 minutes
✓ BIKE_TRANSIT: 8.9 minutes
✓ BICYCLE: 8.9 minutes
✓ CAR: 12.5 minutes


### Extract Geometry for All Routes


In [27]:
# Function to extract coordinates from any route
def extract_route_coordinates(route_data, route_name):
    """Extract coordinates from a route response"""
    coordinates = []
    
    if not route_data or 'plan' not in route_data:
        print(f"No valid route data for {route_name}")
        return coordinates
    
    itinerary = route_data['plan']['itineraries'][0]
    
    for i, leg in enumerate(itinerary['legs']):
        print(f"  {route_name} - Leg {i+1}: {leg['mode']}")
        
        if 'legGeometry' in leg and 'points' in leg['legGeometry']:
            encoded_polyline = leg['legGeometry']['points']
            try:
                decoded_coords = polyline.decode(encoded_polyline)
                coordinates.extend(decoded_coords)
                print(f"    Added {len(decoded_coords)} points")
            except Exception as e:
                print(f"    Error decoding polyline: {e}")
                # Fallback to start/end points
                coordinates.append([leg['from']['lat'], leg['from']['lon']])
                coordinates.append([leg['to']['lat'], leg['to']['lon']])
        else:
            # Fallback to start/end points
            coordinates.append([leg['from']['lat'], leg['from']['lon']])
            coordinates.append([leg['to']['lat'], leg['to']['lon']])
    
    print(f"  Total coordinates for {route_name}: {len(coordinates)}")
    return coordinates

# Extract coordinates for all successful routes
all_route_coordinates = {}

# Include the original walking route
all_route_coordinates['walk'] = route_coordinates

# Extract coordinates for multimodal routes
for mode, route_data in multimodal_routes.items():
    coords = extract_route_coordinates(route_data, mode)
    if coords:
        all_route_coordinates[mode] = coords

print(f"\nSuccessfully extracted coordinates for {len(all_route_coordinates)} routes:")


  transit - Leg 1: WALK
    Added 8 points
  transit - Leg 2: BUS
    Added 6 points
  transit - Leg 3: WALK
    Added 48 points
  Total coordinates for transit: 62
  bike_transit - Leg 1: BICYCLE
    Added 35 points
  bike_transit - Leg 2: BUS
    Added 2 points
  bike_transit - Leg 3: BICYCLE
    Added 117 points
  bike_transit - Leg 4: WALK
    Added 3 points
  Total coordinates for bike_transit: 157
  bicycle - Leg 1: BICYCLE
    Added 151 points
  bicycle - Leg 2: WALK
    Added 3 points
  Total coordinates for bicycle: 154
  car - Leg 1: CAR
    Added 201 points
  Total coordinates for car: 201

Successfully extracted coordinates for 5 routes:


### Multi-Modal Route Comparison Map


In [28]:
# Create a comparison map with all transport modes
center_lat = (from_location.latitude + to_location.latitude) / 2
center_lon = (from_location.longitude + to_location.longitude) / 2

comparison_map = folium.Map(location=[center_lat, center_lon], zoom_start=13)

# Define colors and styles for different modes
mode_styles = {
    'walk': {'color': 'blue', 'weight': 4, 'opacity': 0.8},
    'transit': {'color': 'green', 'weight': 4, 'opacity': 0.7},
    'bike_transit': {'color': 'orange', 'weight': 4, 'opacity': 0.7},
    'bicycle': {'color': 'red', 'weight': 3, 'opacity': 0.8},
    'car': {'color': 'purple', 'weight': 3, 'opacity': 0.6}
}

# Add routes to the map
routes_added = 0
for mode, coordinates in all_route_coordinates.items():
    if coordinates and mode in mode_styles:
        style = mode_styles[mode]
        
        # Get route duration for popup
        duration_text = "N/A"
        if mode == 'walk' and route_data and 'plan' in route_data:
            duration_min = route_data['plan']['itineraries'][0]['duration'] / 60
            duration_text = f"{duration_min:.1f} min"
        elif mode in multimodal_routes and multimodal_routes[mode] and 'plan' in multimodal_routes[mode]:
            duration_min = multimodal_routes[mode]['plan']['itineraries'][0]['duration'] / 60
            duration_text = f"{duration_min:.1f} min"
        
        folium.PolyLine(
            locations=coordinates,
            color=style['color'],
            weight=style['weight'],
            opacity=style['opacity'],
            popup=f"{mode.upper()} route ({duration_text}, {len(coordinates)} points)"
        ).add_to(comparison_map)
        
        routes_added += 1
        print(f"Added {mode} route to map ({len(coordinates)} points)")

# Add markers
folium.Marker(
    [from_location.latitude, from_location.longitude],
    popup="Institute for Transport Studies, Leeds",
    icon=folium.Icon(color='green', icon='play')
).add_to(comparison_map)

folium.Marker(
    [to_location.latitude, to_location.longitude],
    popup="Leeds Railway Station",
    icon=folium.Icon(color='red', icon='stop')
).add_to(comparison_map)

# Add a legend
legend_html = '''
<div style="position: fixed; 
     top: 10px; right: 10px; width: 200px; height: 150px; 
     background-color: white; border:2px solid grey; z-index:9999; 
     font-size:14px; padding: 10px">
<p><b>Route Types</b></p>
<p><i class="fa fa-minus" style="color:blue"></i> Walking</p>
<p><i class="fa fa-minus" style="color:green"></i> Public Transit</p>
<p><i class="fa fa-minus" style="color:orange"></i> Bike + Transit</p>
<p><i class="fa fa-minus" style="color:red"></i> Cycling</p>
<p><i class="fa fa-minus" style="color:purple"></i> Driving</p>
</div>
'''
comparison_map.get_root().html.add_child(folium.Element(legend_html))

print(f"\nComparison map created with {routes_added} routes")
comparison_map


Added walk route to map (122 points)
Added transit route to map (62 points)
Added bike_transit route to map (157 points)
Added bicycle route to map (154 points)
Added car route to map (201 points)

Comparison map created with 5 routes


### Route Comparison Summary


In [29]:
# Create a comprehensive comparison table
comparison_data = []

# Add walking route
if route_data and 'plan' in route_data:
    itinerary = route_data['plan']['itineraries'][0]
    comparison_data.append({
        'Mode': 'Walking',
        'Duration (min)': round(itinerary['duration'] / 60, 1),
        'Distance (m)': round(itinerary.get('walkDistance', 0), 0),
        'Legs': len(itinerary['legs']),
        'Coordinates': len(route_coordinates) if route_coordinates else 0
    })

# Add multimodal routes
for mode, route_data_mm in multimodal_routes.items():
    if route_data_mm and 'plan' in route_data_mm:
        itinerary = route_data_mm['plan']['itineraries'][0]
        
        # Calculate total distance (walk + transit distances)
        total_distance = 0
        walk_distance = itinerary.get('walkDistance', 0)
        transit_distance = 0
        
        for leg in itinerary['legs']:
            if leg['mode'] in ['BUS', 'RAIL', 'SUBWAY', 'TRAM']:
                transit_distance += leg.get('distance', 0)
        
        total_distance = walk_distance + transit_distance
        
        # Get mode details
        modes_in_route = [leg['mode'] for leg in itinerary['legs']]
        mode_display = mode.replace('_', ' + ').title()
        
        comparison_data.append({
            'Mode': f"{mode_display} ({', '.join(set(modes_in_route))})",
            'Duration (min)': round(itinerary['duration'] / 60, 1),
            'Distance (m)': round(total_distance, 0),
            'Legs': len(itinerary['legs']),
            'Coordinates': len(all_route_coordinates.get(mode, [])) if mode in all_route_coordinates else 0
        })

# Create DataFrame and display
if comparison_data:
    comparison_df = pd.DataFrame(comparison_data)
    comparison_df = comparison_df.sort_values('Duration (min)')
    
    print("Route Comparison Summary:")
    print("=" * 80)
    print(comparison_df.to_string(index=False))
    
    # Find fastest and shortest routes
    if len(comparison_df) > 1:
        fastest = comparison_df.iloc[0]
        shortest_by_distance = comparison_df.loc[comparison_df['Distance (m)'].idxmin()]
        
        print(f"\n📊 Analysis:")
        print(f"• Fastest route: {fastest['Mode']} ({fastest['Duration (min)']} min)")
        print(f"• Shortest distance: {shortest_by_distance['Mode']} ({shortest_by_distance['Distance (m)']} m)")
        
        # Calculate time savings
        walking_time = comparison_df[comparison_df['Mode'] == 'Walking']['Duration (min)'].iloc[0] if 'Walking' in comparison_df['Mode'].values else None
        if walking_time and fastest['Mode'] != 'Walking':
            time_saved = walking_time - fastest['Duration (min)']
            print(f"• Time saved vs walking: {time_saved:.1f} minutes ({time_saved/walking_time*100:.1f}%)")

else:
    print("No successful routes to compare")


Route Comparison Summary:
                               Mode  Duration (min)  Distance (m)  Legs  Coordinates
            Bicycle (BICYCLE, WALK)             8.9        2325.0     2          154
Bike + Transit (BUS, BICYCLE, WALK)             8.9        2379.0     4          157
                            Walking            12.5           0.0     1          122
                          Car (CAR)            12.5           0.0     1          201
                Transit (BUS, WALK)            24.3        2615.0     3           62

📊 Analysis:
• Fastest route: Bicycle (BICYCLE, WALK) (8.9 min)
• Shortest distance: Walking (0.0 m)
• Time saved vs walking: 3.6 minutes (28.8%)


## 3. Working with Desire Lines

Desire lines represent travel demand between origin-destination pairs. We'll work with data from the National Trip End Model (NTEM).


### 3.1 Loading OD Data

We'll import and apply basic preprocessing steps to desire lines from NTEM.


In [53]:
# Load desire lines data from NTEM
print("Loading NTEM desire lines data...")
desire_lines_url = "https://github.com/ITSLeeds/TDS/releases/download/22/NTEM_flow.geojson"
desire_lines_raw = gpd.read_file(desire_lines_url)

# Select relevant columns
desire_lines = desire_lines_raw[['from', 'to', 'all', 'walk', 'drive', 'cycle', 'geometry']].copy()

print(f"Loaded {len(desire_lines)} desire lines")
print(f"Columns: {list(desire_lines.columns)}")
print("\nFirst few rows:")
print(desire_lines.head())


Loading NTEM desire lines data...


Loaded 502 desire lines
Columns: ['from', 'to', 'all', 'walk', 'drive', 'cycle', 'geometry']

First few rows:
        from         to     all    walk  drive  cycle  \
0  E02002444  E02002443  1374.0  1121.0   55.0    0.0   
1  E02002443  E02002445  1189.0   868.0  100.0    4.0   
2  E02002442  E02002440  1494.0  1139.0   83.0   23.0   
3  E02002442  E02002441  1747.0   906.0  349.0   62.0   
4  E02002447  E02002448  4930.0  4162.0   70.0   98.0   

                                        geometry  
0  LINESTRING (-1.4755 53.7125, -1.4903 53.7144)  
1  LINESTRING (-1.4903 53.7144, -1.5047 53.7104)  
2   LINESTRING (-1.3374 53.7175, -1.3203 53.721)  
3   LINESTRING (-1.3374 53.7175, -1.3665 53.718)  
4  LINESTRING (-1.2403 53.7065, -1.2657 53.7066)  


In [54]:
# Load zone centroids
print("Loading NTEM centroids...")
centroids_url = "https://github.com/ITSLeeds/TDS/releases/download/22/NTEM_cents.geojson"
centroids = gpd.read_file(centroids_url)

print(f"Loaded {len(centroids)} zone centroids")
print(f"Centroids columns: {list(centroids.columns)}")


Loading NTEM centroids...
Loaded 278 zone centroids
Centroids columns: ['Zone_Code', 'rural_urban', 'region', 'geometry']


In [55]:
centroids.head()

Zone_Code rural_urban                    region                   geometry
0  E02002446       Urban  Yorkshire and The Humber  POINT (-1.42936 53.70823)
1  E02002447       Urban  Yorkshire and The Humber  POINT (-1.24029 53.70647)
2  E02002444       Urban  Yorkshire and The Humber  POINT (-1.47551 53.71247)
3  E02002445       Urban  Yorkshire and The Humber  POINT (-1.50467 53.71042)
4  E02002442       Urban  Yorkshire and The Humber  POINT (-1.33737 53.71751)

### 3.2 Visualizing Desire Lines


In [56]:
# Create a map showing desire lines and centroids
desire_map = folium.Map(location=[53.8, -1.55], zoom_start=8)

# Add desire lines with thickness and color based on total trips
for idx, row in desire_top.iterrows():
    # Get line geometry
    if row.geometry.geom_type == 'LineString':
        coords = [[point[1], point[0]] for point in row.geometry.coords]  # Flip to lat,lon
        
        # Scale line width based on total trips (normalize to 1-10 range)
        max_trips = desire_top['all'].max()
        line_width = 1 + (row['all'] / max_trips) * 9
        
        # Color based on total trips (blue to red scale)
        color_intensity = row['all'] / max_trips
        color = f"rgb({int(255 * color_intensity)}, {int(100 * (1 - color_intensity))}, {int(255 * (1 - color_intensity))})"
        
        folium.PolyLine(
            locations=coords,
            weight=line_width,
            color=color,
            opacity=0.8,
            popup=f"From: {row['from']} to {row['to']}<br>Total trips: {row['all']:,.0f}<br>Drive: {row['drive']:,.0f}<br>Walk: {row['walk']:,.0f}<br>Cycle: {row['cycle']:,.0f}"
        ).add_to(desire_map)

# Add centroids for the zones involved in top desire lines
# Since 'geo_code' is not a column, try to use the index or another identifier
# We'll assume the index of centroids corresponds to the zone code
involved_zones = set(desire_top['from'].tolist() + desire_top['to'].tolist())

# Try to find the correct column for zone code
centroid_id_col = None
for col in centroids.columns:
    if col.lower() in ['zone', 'zone_code', 'code', 'id', 'geo_code']:
        centroid_id_col = col
        break

if centroid_id_col is not None:
    centroids_subset = centroids[centroids[centroid_id_col].isin(involved_zones)]
else:
    # Fallback: try to use the index as the zone code
    centroids_subset = centroids.loc[centroids.index.isin(involved_zones)]

for idx, centroid in centroids_subset.iterrows():
    if centroid.geometry.geom_type == 'Point':
        lat, lon = centroid.geometry.y, centroid.geometry.x
        # Use the identifier for popup
        zone_id = centroid[centroid_id_col] if centroid_id_col is not None else idx
        folium.CircleMarker(
            location=[lat, lon],
            radius=3,
            color='red',
            fill=True,
            fillColor='red',
            fillOpacity=0.7,
            popup=f"Zone: {zone_id}"
        ).add_to(desire_map)

print("Desire lines map created")
desire_map


Desire lines map created


### 3.3 Extract Start and End Points


In [40]:
# Extract start and end points from desire lines
from_points = []
to_points = []

for idx, row in desire_top.iterrows():
    if row.geometry.geom_type == 'LineString':
        # Get start point (first coordinate)
        start_coord = row.geometry.coords[0]  # (lon, lat)
        from_points.append({
            'id': row['from'],
            'lat': start_coord[1],
            'lon': start_coord[0],
            'trips': row['all']
        })
        
        # Get end point (last coordinate)
        end_coord = row.geometry.coords[-1]  # (lon, lat)
        to_points.append({
            'id': row['to'],
            'lat': end_coord[1],
            'lon': end_coord[0],
            'trips': row['all']
        })

# Create DataFrames
from_places_df = pd.DataFrame(from_points)
to_places_df = pd.DataFrame(to_points)

print("Origin points:")
print(from_places_df)
print("\nDestination points:")
print(to_places_df)


Origin points:
          id      lat     lon    trips
0  E02006875  53.7979 -1.5470  13432.0
1  E02006875  53.7979 -1.5470  11315.0
2  E02006876  53.7817 -1.5302  10314.0
3  E02002226  53.7879 -1.7749   8635.0
4  E02002191  53.8649 -1.9226   7091.0

Destination points:
          id      lat     lon    trips
0  E02002392  53.8034 -1.5624  13432.0
1  E02002393  53.8043 -1.5237  11315.0
2  E02006875  53.7979 -1.5470  10314.0
3  E02002221  53.7981 -1.7469   8635.0
4  E02002190  53.8700 -1.9007   7091.0


### 3.4 Calculating Routes for Desire Lines


In [41]:
# Calculate driving routes for the top desire lines
print("Calculating driving routes for desire lines...")

routes_drive_top = []
route_coordinates_drive = []

for i, (from_point, to_point) in enumerate(zip(from_points, to_points)):
    print(f"Planning route {i+1}/5: {from_point['id']} -> {to_point['id']}")
    
    # Plan driving route
    route_data = otp_plan(
        from_lat=from_point['lat'],
        from_lon=from_point['lon'],
        to_lat=to_point['lat'],
        to_lon=to_point['lon'],
        mode="CAR"
    )
    
    if route_data and 'plan' in route_data:
        itinerary = route_data['plan']['itineraries'][0]
        duration_min = itinerary['duration'] / 60
        total_distance = sum(leg.get('distance', 0) for leg in itinerary['legs'])
        
        routes_drive_top.append({
            'from_id': from_point['id'],
            'to_id': to_point['id'],
            'trips': from_point['trips'],
            'duration_min': duration_min,
            'distance_m': total_distance,
            'route_data': route_data
        })
        
        # Extract route coordinates
        coords = extract_route_coordinates(route_data, f"{from_point['id']}->{to_point['id']}")
        if coords:
            route_coordinates_drive.append(coords)
        
        print(f"  ✓ Route found: {duration_min:.1f} min, {total_distance:.0f}m")
    else:
        print(f"  ✗ No route found")
        routes_drive_top.append({
            'from_id': from_point['id'],
            'to_id': to_point['id'],
            'trips': from_point['trips'],
            'duration_min': None,
            'distance_m': None,
            'route_data': None
        })

print(f"\nSuccessfully calculated {len([r for r in routes_drive_top if r['route_data']])} out of {len(routes_drive_top)} routes")


Calculating driving routes for desire lines...
Planning route 1/5: E02006875 -> E02002392
  E02006875->E02002392 - Leg 1: CAR
    Added 82 points
  Total coordinates for E02006875->E02002392: 82
  ✓ Route found: 6.7 min, 1536m
Planning route 2/5: E02006875 -> E02002393
  E02006875->E02002393 - Leg 1: CAR
    Added 116 points
  Total coordinates for E02006875->E02002393: 116
  ✓ Route found: 10.9 min, 2482m
Planning route 3/5: E02006876 -> E02006875
  E02006876->E02006875 - Leg 1: CAR
    Added 182 points
  Total coordinates for E02006876->E02006875: 182
  ✓ Route found: 13.8 min, 3106m
Planning route 4/5: E02002226 -> E02002221
  E02002226->E02002221 - Leg 1: CAR
    Added 112 points
  Total coordinates for E02002226->E02002221: 112
  ✓ Route found: 11.2 min, 3005m
Planning route 5/5: E02002191 -> E02002190
  E02002191->E02002190 - Leg 1: CAR
    Added 62 points
  Total coordinates for E02002191->E02002190: 62
  ✓ Route found: 6.9 min, 1834m

Successfully calculated 5 out of 5 routes


### 3.5 Visualizing Routes vs Desire Lines


In [42]:
# Create a map comparing desire lines with actual routes
comparison_routes_map = folium.Map(location=[53.8, -1.55], zoom_start=8)

# Add desire lines (in red/orange)
for idx, row in desire_top.iterrows():
    if row.geometry.geom_type == 'LineString':
        coords = [[point[1], point[0]] for point in row.geometry.coords]
        
        folium.PolyLine(
            locations=coords,
            weight=3,
            color='red',
            opacity=0.7,
            popup=f"Desire Line<br>From: {row['from']} to {row['to']}<br>Total trips: {row['all']:,.0f}"
        ).add_to(comparison_routes_map)

# Add calculated routes (in blue)
for i, (route_info, coords) in enumerate(zip(routes_drive_top, route_coordinates_drive)):
    if route_info['route_data'] and coords:
        folium.PolyLine(
            locations=coords,
            weight=2,
            color='blue',
            opacity=0.8,
            popup=f"Driving Route<br>From: {route_info['from_id']} to {route_info['to_id']}<br>Duration: {route_info['duration_min']:.1f} min<br>Distance: {route_info['distance_m']:,.0f}m"
        ).add_to(comparison_routes_map)

# Add origin and destination markers
for from_point in from_points:
    folium.Marker(
        location=[from_point['lat'], from_point['lon']],
        popup=f"Origin: {from_point['id']}<br>Trips: {from_point['trips']:,.0f}",
        icon=folium.Icon(color='green', icon='play')
    ).add_to(comparison_routes_map)

for to_point in to_points:
    folium.Marker(
        location=[to_point['lat'], to_point['lon']],
        popup=f"Destination: {to_point['id']}<br>Trips: {to_point['trips']:,.0f}",
        icon=folium.Icon(color='red', icon='stop')
    ).add_to(comparison_routes_map)

# Add legend
routes_legend_html = '''
<div style="position: fixed; 
     top: 10px; right: 10px; width: 180px; height: 120px; 
     background-color: white; border:2px solid grey; z-index:9999; 
     font-size:14px; padding: 10px">
<p><b>Routes vs Desire Lines</b></p>
<p><i class="fa fa-minus" style="color:red"></i> Desire Lines</p>
<p><i class="fa fa-minus" style="color:blue"></i> Driving Routes</p>
<p><i class="fa fa-play" style="color:green"></i> Origins</p>
<p><i class="fa fa-stop" style="color:red"></i> Destinations</p>
</div>
'''
comparison_routes_map.get_root().html.add_child(folium.Element(routes_legend_html))

print("Routes vs desire lines comparison map created")
comparison_routes_map


Routes vs desire lines comparison map created


## 4. Route Network Analysis

Route networks aggregate individual routes to show cumulative traffic flow by combining overlapping route segments.


### 4.1 Loading Comprehensive Route Data


In [44]:
# Load more comprehensive route data
print("Loading comprehensive route datasets...")

routes_drive_url = "https://github.com/ITSLeeds/TDS/releases/download/22/routes_drive.geojson"
routes_transit_url = "https://github.com/ITSLeeds/TDS/releases/download/22/routes_transit.geojson"

print("Loading driving routes...")
routes_drive = gpd.read_file(routes_drive_url)

print("Loading transit routes...")
routes_transit = gpd.read_file(routes_transit_url)

# Check the dimensions and structure of these datasets
print(f"\nDataset dimensions:")
print(f"Desire lines: {desire_lines.shape} - Columns: {list(desire_lines.columns)}")
print(f"Routes drive: {routes_drive.shape} - Columns: {list(routes_drive.columns)}")
print(f"Routes transit: {routes_transit.shape} - Columns: {list(routes_transit.columns)}")

print(f"\nFirst few rows of routes_drive:")
print(routes_drive.head())


Loading comprehensive route datasets...
Loading driving routes...
Loading transit routes...

Dataset dimensions:
Desire lines: (502, 7) - Columns: ['from', 'to', 'all', 'walk', 'drive', 'cycle', 'geometry']
Routes drive: (502, 33) - Columns: ['fromPlace', 'toPlace', 'duration', 'startTime', 'endTime', 'walkTime', 'transitTime', 'waitingTime', 'walkDistance', 'walkLimitExceeded', 'elevationLost', 'elevationGained', 'transfers', 'tooSloped', 'fare', 'fare_currency', 'route_option', 'leg_startTime', 'leg_endTime', 'departureDelay', 'arrivalDelay', 'realTime', 'distance', 'pathway', 'mode', 'route', 'agencyTimeZoneOffset', 'interlineWithPreviousLeg', 'rentedBike', 'flexDrtAdvanceBookMin', 'leg_duration', 'transitLeg', 'geometry']
Routes transit: (4718, 42) - Columns: ['fromPlace', 'toPlace', 'duration', 'startTime', 'endTime', 'walkTime', 'transitTime', 'waitingTime', 'walkDistance', 'walkLimitExceeded', 'elevationLost', 'elevationGained', 'transfers', 'tooSloped', 'fare', 'fare_currency',

### 4.2 Joining Routes with Desire Lines Data


In [45]:
# Join routes with desire lines data to get trip counts
print("Joining routes with desire lines data...")

# Prepare routes data by renaming columns to match desire lines
routes_drive_prep = routes_drive.copy()
if 'fromPlace' in routes_drive_prep.columns:
    routes_drive_prep = routes_drive_prep.rename(columns={'fromPlace': 'from', 'toPlace': 'to'})

routes_transit_prep = routes_transit.copy()
if 'fromPlace' in routes_transit_prep.columns:
    routes_transit_prep = routes_transit_prep.rename(columns={'fromPlace': 'from', 'toPlace': 'to'})

# Create a version of desire lines without geometry for joining
desire_lines_data = desire_lines.drop(columns=['geometry'])

# Join routes with desire lines data
print("Joining driving routes...")
routes_drive_joined = routes_drive_prep.merge(
    desire_lines_data, 
    on=['from', 'to'], 
    how='left'
)

print("Joining transit routes...")
routes_transit_joined = routes_transit_prep.merge(
    desire_lines_data, 
    on=['from', 'to'], 
    how='left'
)

print(f"\nJoined datasets:")
print(f"Routes drive joined: {routes_drive_joined.shape}")
print(f"Routes transit joined: {routes_transit_joined.shape}")

# Check for successful joins
drive_joined_count = routes_drive_joined['drive'].notna().sum()
transit_joined_count = routes_transit_joined['all'].notna().sum()

print(f"\nSuccessful joins:")
print(f"Driving routes with trip data: {drive_joined_count}/{len(routes_drive_joined)}")
print(f"Transit routes with trip data: {transit_joined_count}/{len(routes_transit_joined)}")

# Show sample of joined data
print(f"\nSample of joined driving routes:")
print(routes_drive_joined[['from', 'to', 'drive', 'all']].head())


Joining routes with desire lines data...
Joining driving routes...
Joining transit routes...

Joined datasets:
Routes drive joined: (502, 37)
Routes transit joined: (4718, 46)

Successful joins:
Driving routes with trip data: 502/502
Transit routes with trip data: 4718/4718

Sample of joined driving routes:
        from         to  drive     all
0  E02002444  E02002443   55.0  1374.0
1  E02002443  E02002445  100.0  1189.0
2  E02002442  E02002440   83.0  1494.0
3  E02002442  E02002441  349.0  1747.0
4  E02002447  E02002448   70.0  4930.0


### 4.3 Creating Route Networks by Aggregating Overlapping Routes


In [46]:
# Create route network by aggregating overlapping routes
# This is a simplified version of the R 'overline' function
print("Creating route networks by aggregating overlapping routes...")

def create_route_network(routes_gdf, value_column='drive', buffer_distance=50):
    """
    Create a route network by aggregating overlapping routes.
    This is a simplified version of the R stplanr::overline function.
    """
    # Filter out routes with no trip data
    routes_with_data = routes_gdf[routes_gdf[value_column].notna()].copy()
    
    if len(routes_with_data) == 0:
        print(f"No routes with {value_column} data found")
        return gpd.GeoDataFrame()
    
    print(f"Processing {len(routes_with_data)} routes with {value_column} data...")
    
    # For simplicity, we'll create a basic aggregation
    # In a full implementation, this would involve spatial overlay operations
    # to properly merge overlapping route segments
    
    # Group by similar start/end points (simplified approach)
    routes_with_data['route_id'] = range(len(routes_with_data))
    
    # Create a simple network by keeping routes with significant traffic
    min_threshold = routes_with_data[value_column].quantile(0.1)  # Bottom 10%
    significant_routes = routes_with_data[routes_with_data[value_column] >= min_threshold].copy()
    
    print(f"Keeping {len(significant_routes)} routes above threshold ({min_threshold:.0f} trips)")
    
    return significant_routes

# Create driving route network
rnet_drive = create_route_network(routes_drive_joined, 'drive')

# Create transit route network (using 'all' trips since it's multimodal)
rnet_transit = create_route_network(routes_transit_joined, 'all')

print(f"\nRoute networks created:")
print(f"Driving network: {len(rnet_drive)} routes")
print(f"Transit network: {len(rnet_transit)} routes")

if len(rnet_drive) > 0:
    print(f"\nDriving network statistics:")
    print(f"Total driving trips: {rnet_drive['drive'].sum():,.0f}")
    print(f"Average trips per route: {rnet_drive['drive'].mean():.0f}")
    print(f"Max trips on single route: {rnet_drive['drive'].max():.0f}")
    
if len(rnet_transit) > 0:
    print(f"\nTransit network statistics:")
    print(f"Total transit trips: {rnet_transit['all'].sum():,.0f}")
    print(f"Average trips per route: {rnet_transit['all'].mean():.0f}")
    print(f"Max trips on single route: {rnet_transit['all'].max():.0f}")


Creating route networks by aggregating overlapping routes...
Processing 502 routes with drive data...
Keeping 451 routes above threshold (105 trips)
Processing 4718 routes with all data...
Keeping 4258 routes above threshold (1140 trips)

Route networks created:
Driving network: 451 routes
Transit network: 4258 routes

Driving network statistics:
Total driving trips: 204,404
Average trips per route: 453
Max trips on single route: 2346

Transit network statistics:
Total transit trips: 9,041,075
Average trips per route: 2123
Max trips on single route: 13432


In [52]:
# Visualize route networks
print("Creating route network visualizations...")

# Create a map for driving route network
if len(rnet_drive) > 0:
    print(f"Creating driving route network map...")
    
    # Calculate map center
    bounds = rnet_drive.total_bounds
    center_lat = (bounds[1] + bounds[3]) / 2
    center_lon = (bounds[0] + bounds[2]) / 2
    
    # Create map
    rnet_drive_map = folium.Map(location=[center_lat, center_lon], zoom_start=9)
    
    # Define color scheme based on trip volumes (like viridis)
    min_trips = rnet_drive['drive'].min()
    max_trips = rnet_drive['drive'].max()
    
    def get_color_and_width(trips):
        """Get color and line width based on trip volume"""
        # Normalize trips to 0-1 scale
        if max_trips > min_trips:
            normalized = (trips - min_trips) / (max_trips - min_trips)
        else:
            normalized = 0.5
        
        # Create color gradient (blue to yellow to red, like viridis)
        if normalized < 0.5:
            # Blue to green
            r = int(68 * (normalized * 2))
            g = int(1 + (158 * normalized * 2))
            b = int(84 + (99 * (1 - normalized * 2)))
        else:
            # Green to yellow to red
            r = int(158 + (97 * (normalized - 0.5) * 2))
            g = int(158 + (97 * (normalized - 0.5) * 2))
            b = int(183 * (1 - (normalized - 0.5) * 2))
        
        color = f'#{r:02x}{g:02x}{b:02x}'
        
        # Line width based on trip volume (1-8 pixels)
        width = 1 + (normalized * 7)
        
        return color, width
    
    # Add routes to map
    for idx, route in rnet_drive.iterrows():
        if route.geometry.geom_type == 'LineString':
            coords = [[point[1], point[0]] for point in route.geometry.coords]
            trips = route['drive']
            color, width = get_color_and_width(trips)
            
            folium.PolyLine(
                locations=coords,
                color=color,
                weight=width,
                opacity=0.8,
                popup=f"Route: {route.get('from', 'Unknown')} → {route.get('to', 'Unknown')}<br>Driving trips: {trips:,.0f}"
            ).add_to(rnet_drive_map)
    
    # Add legend for driving network
    drive_legend_html = f'''
    <div style="position: fixed; 
         top: 10px; right: 10px; width: 200px; height: 100px; 
         background-color: white; border:2px solid grey; z-index:9999; 
         font-size:12px; padding: 10px">
    <p><b>Driving Route Network</b></p>
    <p>Trip Volume:</p>
    <p>Min: {min_trips:,.0f} trips</p>
    <p>Max: {max_trips:,.0f} trips</p>
    <p>Routes: {len(rnet_drive)}</p>
    </div>
    '''
    rnet_drive_map.get_root().html.add_child(folium.Element(drive_legend_html))
    
    print("Driving route network map created")
    
else:
    print("No driving route network data to visualize")
    rnet_drive_map = None

# Display the driving network map
if rnet_drive_map:
    rnet_drive_map
else:
    print("No driving route network map to display")

Creating route network visualizations...
Creating driving route network map...
Driving route network map created


In [68]:

# Create transit route network visualization
if len(rnet_transit) > 0:
    print(f"Creating transit route network map...")
    
    # Calculate map center
    bounds = rnet_transit.total_bounds
    center_lat = (bounds[1] + bounds[3]) / 2
    center_lon = (bounds[0] + bounds[2]) / 2
    
    # Create map
    rnet_transit_map = folium.Map(location=[center_lat, center_lon], zoom_start=9)
    
    # Define color scheme for transit
    min_trips = rnet_transit['all'].min()
    max_trips = rnet_transit['all'].max()
    
    # Add routes to map
    for idx, route in rnet_transit.iterrows():
        if route.geometry.geom_type == 'LineString':
            coords = [[point[1], point[0]] for point in route.geometry.coords]
            trips = route['all']
            
            # Different color scheme for transit (green-based)
            if max_trips > min_trips:
                normalized = (trips - min_trips) / (max_trips - min_trips)
            else:
                normalized = 0.5
            
            # Green color gradient
            r = int(50 + (100 * (1 - normalized)))
            g = int(150 + (105 * normalized))
            b = int(50 + (50 * (1 - normalized)))
            color = f'#{r:02x}{g:02x}{b:02x}'
            
            width = 1 + (normalized * 6)
            
            folium.PolyLine(
                locations=coords,
                color=color,
                weight=width,
                opacity=0.7,
                popup=f"Route: {route.get('from', 'Unknown')} → {route.get('to', 'Unknown')}<br>Total trips: {trips:,.0f}<br>Walk: {route.get('walk', 0):,.0f} | Drive: {route.get('drive', 0):,.0f}"
            ).add_to(rnet_transit_map)
    
    # Add legend for transit network
    transit_legend_html = f'''
    <div style="position: fixed; 
         top: 10px; right: 10px; width: 200px; height: 100px; 
         background-color: white; border:2px solid grey; z-index:9999; 
         font-size:12px; padding: 10px">
    <p><b>Transit Route Network</b></p>
    <p>Trip Volume:</p>
    <p>Min: {min_trips:,.0f} trips</p>
    <p>Max: {max_trips:,.0f} trips</p>
    <p>Routes: {len(rnet_transit)}</p>
    </div>
    '''
    rnet_transit_map.get_root().html.add_child(folium.Element(transit_legend_html))
    
    print("Transit route network map created")
    display(rnet_transit_map)  # Ensure map is displayed in notebook output

    
else:
    print("No transit route network data to visualize")
    rnet_transit_map = None

# Display the transit network map
if rnet_transit_map:
    rnet_transit_map
else:
    print("No transit route network map to display")


Creating transit route network map...
Transit route network map created


In [49]:
# Summary of route networks
print("Route Network Analysis Summary:")
print("=" * 60)

if len(rnet_drive) > 0:
    print(f"\n🚗 Driving Route Network:")
    print(f"  • Total routes: {len(rnet_drive):,}")
    print(f"  • Total driving trips: {rnet_drive['drive'].sum():,.0f}")
    print(f"  • Average trips per route: {rnet_drive['drive'].mean():.0f}")
    print(f"  • Busiest route: {rnet_drive['drive'].max():,.0f} trips")
    print(f"  • Route density: {len(rnet_drive) / rnet_drive['drive'].sum() * 1000:.1f} routes per 1000 trips")

if len(rnet_transit) > 0:
    print(f"\n🚌 Transit Route Network:")
    print(f"  • Total routes: {len(rnet_transit):,}")
    print(f"  • Total trips: {rnet_transit['all'].sum():,.0f}")
    print(f"  • Average trips per route: {rnet_transit['all'].mean():.0f}")
    print(f"  • Busiest route: {rnet_transit['all'].max():,.0f} trips")
    print(f"  • Route density: {len(rnet_transit) / rnet_transit['all'].sum() * 1000:.1f} routes per 1000 trips")

# Compare networks if both exist
if len(rnet_drive) > 0 and len(rnet_transit) > 0:
    print(f"\n📊 Network Comparison:")
    drive_total = rnet_drive['drive'].sum()
    transit_total = rnet_transit['all'].sum()
    
    print(f"  • Driving vs Transit trips: {drive_total:,.0f} vs {transit_total:,.0f}")
    print(f"  • Mode split: {drive_total/(drive_total + transit_total)*100:.1f}% driving, {transit_total/(drive_total + transit_total)*100:.1f}% transit")
    print(f"  • Network efficiency: {len(rnet_drive)/drive_total*1000:.2f} vs {len(rnet_transit)/transit_total*1000:.2f} routes per 1000 trips")

print(f"\n✅ Route network analysis complete!")


Route Network Analysis Summary:

🚗 Driving Route Network:
  • Total routes: 451
  • Total driving trips: 204,404
  • Average trips per route: 453
  • Busiest route: 2,346 trips
  • Route density: 2.2 routes per 1000 trips

🚌 Transit Route Network:
  • Total routes: 4,258
  • Total trips: 9,041,075
  • Average trips per route: 2123
  • Busiest route: 13,432 trips
  • Route density: 0.5 routes per 1000 trips

📊 Network Comparison:
  • Driving vs Transit trips: 204,404 vs 9,041,075
  • Mode split: 2.2% driving, 97.8% transit
  • Network efficiency: 2.21 vs 0.47 routes per 1000 trips

✅ Route network analysis complete!


In [66]:
# Summary of routes vs desire lines
routes_summary = pd.DataFrame(routes_drive_top)
routes_summary = routes_summary[routes_summary['route_data'].notna()]  # Only successful routes

print("Route Summary:")
print("=" * 60)
print(routes_summary[['from_id', 'to_id', 'trips', 'duration_min', 'distance_m']].to_string(index=False))

if len(routes_summary) > 0:
    print(f"\nAnalysis:")
    print(f"• Average route duration: {routes_summary['duration_min'].mean():.1f} minutes")
    print(f"• Average route distance: {routes_summary['distance_m'].mean():,.0f} meters")
    print(f"• Total trips represented: {routes_summary['trips'].sum():,.0f}")
    print(f"• Routes calculated successfully: {len(routes_summary)}/5")
else:
    print("\nNo successful routes calculated")


Route Summary:
  from_id     to_id   trips  duration_min  distance_m
E02006875 E02002392 13432.0      6.700000    1536.396
E02006875 E02002393 11315.0     10.883333    2482.485
E02006876 E02006875 10314.0     13.850000    3106.262
E02002226 E02002221  8635.0     11.183333    3005.163
E02002191 E02002190  7091.0      6.866667    1833.839

Analysis:
• Average route duration: 9.9 minutes
• Average route distance: 2,393 meters
• Total trips represented: 50,787
• Routes calculated successfully: 5/5


### 5.1 Setup and API Configuration

We'll use the Google Maps Directions API to get routes with real-time traffic data between University of Surrey and Guildford Rail Station.


In [58]:
# Install required package for Google Maps API
# %pip install googlemaps python-dotenv

import googlemaps
import os
from dotenv import load_dotenv
from datetime import datetime, timedelta
import time

# Load environment variables
load_dotenv()

# Get Google Maps API key
GOOGLE_API_KEY = os.getenv('GOOGLE_ROUTES')

if not GOOGLE_API_KEY:
    print("⚠️  Warning: GOOGLE_ROUTES API key not found in .env file")
    print("Please add your Google Maps API key to the .env file as: GOOGLE_ROUTES=your_api_key")
else:
    print("✅ Google Maps API key loaded successfully")

# Initialize Google Maps client
gmaps = googlemaps.Client(key=GOOGLE_API_KEY)


✅ Google Maps API key loaded successfully


In [59]:
# Define origin and destination for Google Maps routing
print("Setting up locations for Google Maps routing...")

# University of Surrey
origin = "University of Surrey, Guildford, UK"
# Guildford Rail Station  
destination = "Guildford Railway Station, Guildford, UK"

print(f"Origin: {origin}")
print(f"Destination: {destination}")

# Geocode the locations to get coordinates
try:
    origin_geocode = gmaps.geocode(origin)[0]
    dest_geocode = gmaps.geocode(destination)[0]
    
    origin_coords = origin_geocode['geometry']['location']
    dest_coords = dest_geocode['geometry']['location']
    
    print(f"\nOrigin coordinates: {origin_coords['lat']:.6f}, {origin_coords['lng']:.6f}")
    print(f"Destination coordinates: {dest_coords['lat']:.6f}, {dest_coords['lng']:.6f}")
    print(f"Formatted addresses:")
    print(f"  Origin: {origin_geocode['formatted_address']}")
    print(f"  Destination: {dest_geocode['formatted_address']}")
    
except Exception as e:
    print(f"Error geocoding locations: {e}")
    origin_coords = None
    dest_coords = None


Setting up locations for Google Maps routing...
Origin: University of Surrey, Guildford, UK
Destination: Guildford Railway Station, Guildford, UK

Origin coordinates: 51.243143, -0.589466
Destination coordinates: 51.236685, -0.580323
Formatted addresses:
  Origin: Stag Hill, University Campus, Guildford GU2 7XH, UK
  Destination: Guildford, Guildford GU1 4UT, UK


### 5.2 Walking Route (Reproducing OTP Route)


In [60]:
# Get walking directions using Google Maps
print("Getting walking directions from Google Maps...")

try:
    # Get walking route
    walking_result = gmaps.directions(
        origin=origin,
        destination=destination,
        mode="walking",
        alternatives=False,  # Get single best route
        departure_time=datetime.now()
    )
    
    if walking_result:
        route = walking_result[0]  # Get first (and only) route
        leg = route['legs'][0]     # Get first leg
        
        print("✅ Walking route retrieved successfully!")
        print(f"Distance: {leg['distance']['text']} ({leg['distance']['value']} meters)")
        print(f"Duration: {leg['duration']['text']} ({leg['duration']['value']} seconds)")
        print(f"Start address: {leg['start_address']}")
        print(f"End address: {leg['end_address']}")
        
        # Extract route polyline for visualization
        walking_polyline = route['overview_polyline']['points']
        
    else:
        print("❌ No walking route found")
        walking_result = None
        
except Exception as e:
    print(f"Error getting walking directions: {e}")
    walking_result = None


Getting walking directions from Google Maps...
✅ Walking route retrieved successfully!
Distance: 0.8 km (838 meters)
Duration: 11 mins (686 seconds)
Start address: Stag Hill, University Campus, Guildford GU2 7XH, UK
End address: Guildford, Guildford GU1 4UT, UK


### 5.3 Driving Routes with Traffic Data


In [61]:
# Get driving directions with traffic data
print("Getting driving directions with traffic data...")

# Get current time for departure
departure_time = datetime.now()
print(f"Departure time: {departure_time.strftime('%Y-%m-%d %H:%M:%S')}")

try:
    # Get driving route with traffic - best guess
    driving_result_best = gmaps.directions(
        origin=origin,
        destination=destination,
        mode="driving",
        departure_time=departure_time,
        traffic_model="best_guess",  # Realistic traffic estimate
        alternatives=True  # Get alternative routes
    )
    
    # Get driving route with traffic - pessimistic
    driving_result_pessimistic = gmaps.directions(
        origin=origin,
        destination=destination,
        mode="driving",
        departure_time=departure_time,
        traffic_model="pessimistic",  # Worst-case traffic
        alternatives=False
    )
    
    # Get driving route with traffic - optimistic
    driving_result_optimistic = gmaps.directions(
        origin=origin,
        destination=destination,
        mode="driving",
        departure_time=departure_time,
        traffic_model="optimistic",  # Best-case traffic
        alternatives=False
    )
    
    print("✅ Driving routes retrieved successfully!")
    
    # Process results
    traffic_results = {
        'best_guess': driving_result_best,
        'pessimistic': driving_result_pessimistic,
        'optimistic': driving_result_optimistic
    }
    
    # Display traffic comparison
    print(f"\n🚗 Traffic Model Comparison:")
    print("=" * 60)
    
    for model_name, result in traffic_results.items():
        if result:
            route = result[0]  # Get first route
            leg = route['legs'][0]
            
            duration_text = leg['duration']['text']
            duration_value = leg['duration']['value']
            
            # Get duration in traffic if available
            if 'duration_in_traffic' in leg:
                traffic_duration_text = leg['duration_in_traffic']['text']
                traffic_duration_value = leg['duration_in_traffic']['value']
                traffic_delay = traffic_duration_value - duration_value
                
                print(f"{model_name.upper()}:")
                print(f"  Duration (no traffic): {duration_text}")
                print(f"  Duration (with traffic): {traffic_duration_text}")
                print(f"  Traffic delay: {traffic_delay} seconds ({traffic_delay/60:.1f} min)")
                print(f"  Distance: {leg['distance']['text']}")
            else:
                print(f"{model_name.upper()}:")
                print(f"  Duration: {duration_text}")
                print(f"  Distance: {leg['distance']['text']}")
            
            print()
            
    # Store best guess result for visualization
    driving_result = driving_result_best
    
except Exception as e:
    print(f"Error getting driving directions: {e}")
    driving_result = None
    traffic_results = {}


Getting driving directions with traffic data...
Departure time: 2025-09-19 12:37:58
✅ Driving routes retrieved successfully!

🚗 Traffic Model Comparison:
BEST_GUESS:
  Duration (no traffic): 5 mins
  Duration (with traffic): 5 mins
  Traffic delay: 23 seconds (0.4 min)
  Distance: 2.0 km

PESSIMISTIC:
  Duration (no traffic): 5 mins
  Duration (with traffic): 7 mins
  Traffic delay: 144 seconds (2.4 min)
  Distance: 2.0 km

OPTIMISTIC:
  Duration (no traffic): 5 mins
  Duration (with traffic): 4 mins
  Traffic delay: -25 seconds (-0.4 min)
  Distance: 2.0 km



### 5.4 Route Visualization


In [ ]:
# Function to decode Google Maps polyline
def decode_polyline(polyline_str):
    """Decode a polyline string into a list of lat/lng coordinates"""
    import polyline
    return polyline.decode(polyline_str)

# Create visualization of Google Maps routes
print("Creating route visualization...")

from IPython.display import display

if walking_result and driving_result and origin_coords and dest_coords:
    # Create map centered between origin and destination
    center_lat = (origin_coords['lat'] + dest_coords['lat']) / 2
    center_lng = (origin_coords['lng'] + dest_coords['lng']) / 2

    gmaps_routes_map = folium.Map(location=[center_lat, center_lng], zoom_start=14)

    # Add walking route
    if walking_result:
        walking_coords = decode_polyline(walking_result[0]['overview_polyline']['points'])
        folium.PolyLine(
            locations=walking_coords,
            color='blue',
            weight=4,
            opacity=0.8,
            popup=f"Walking Route<br>Distance: {walking_result[0]['legs'][0]['distance']['text']}<br>Duration: {walking_result[0]['legs'][0]['duration']['text']}"
        ).add_to(gmaps_routes_map)

    # Add driving routes (alternatives)
    if driving_result:
        colors = ['red', 'orange', 'purple', 'green']  # Colors for different route alternatives

        for i, route in enumerate(driving_result[:4]):  # Max 4 alternatives
            driving_coords = decode_polyline(route['overview_polyline']['points'])
            leg = route['legs'][0]

            # Get traffic duration if available
            if 'duration_in_traffic' in leg:
                duration_text = f"{leg['duration']['text']} (no traffic) / {leg['duration_in_traffic']['text']} (with traffic)"
            else:
                duration_text = leg['duration']['text']

            folium.PolyLine(
                locations=driving_coords,
                color=colors[i],
                weight=3,
                opacity=0.7,
                popup=f"Driving Route {i+1}<br>Distance: {leg['distance']['text']}<br>Duration: {duration_text}"
            ).add_to(gmaps_routes_map)

    # Add origin and destination markers
    folium.Marker(
        [origin_coords['lat'], origin_coords['lng']],
        popup=f"Origin: {origin}",
        icon=folium.Icon(color='green', icon='play')
    ).add_to(gmaps_routes_map)

    folium.Marker(
        [dest_coords['lat'], dest_coords['lng']],
        popup=f"Destination: {destination}",
        icon=folium.Icon(color='red', icon='stop')
    ).add_to(gmaps_routes_map)

    # Add legend
    legend_html = '''
    <div style="position: fixed; 
         top: 10px; right: 10px; width: 180px; height: 120px; 
         background-color: white; border:2px solid grey; z-index:9999; 
         font-size:12px; padding: 10px">
    <p><b>Google Maps Routes</b></p>
    <p><i class="fa fa-minus" style="color:blue"></i> Walking</p>
    <p><i class="fa fa-minus" style="color:red"></i> Driving (Route 1)</p>
    <p><i class="fa fa-minus" style="color:orange"></i> Driving (Route 2)</p>
    <p><i class="fa fa-play" style="color:green"></i> Origin</p>
    <p><i class="fa fa-stop" style="color:red"></i> Destination</p>
    </div>
    '''
    gmaps_routes_map.get_root().html.add_child(folium.Element(legend_html))

    print("✅ Route visualization created successfully!")
    display(gmaps_routes_map)  # Ensure map is displayed in notebook output

else:
    print("❌ Cannot create visualization - missing route data or coordinates")
    gmaps_routes_map = None


Creating route visualization...
✅ Route visualization created successfully!


### 5.5 Detailed Route Analysis


In [63]:
# Analyze route segments and traffic insights
print("Analyzing route segments and traffic data...")

if driving_result:
    print("\n🔍 Detailed Route Analysis:")
    print("=" * 80)
    
    # Analyze each alternative route
    route_analysis = []
    
    for i, route in enumerate(driving_result):
        leg = route['legs'][0]
        
        # Basic route info
        route_info = {
            'route_number': i + 1,
            'distance_text': leg['distance']['text'],
            'distance_meters': leg['distance']['value'],
            'duration_text': leg['duration']['text'],
            'duration_seconds': leg['duration']['value'],
            'summary': route.get('summary', 'Route via main roads')
        }
        
        # Traffic info if available
        if 'duration_in_traffic' in leg:
            route_info['traffic_duration_text'] = leg['duration_in_traffic']['text']
            route_info['traffic_duration_seconds'] = leg['duration_in_traffic']['value']
            route_info['traffic_delay_seconds'] = leg['duration_in_traffic']['value'] - leg['duration']['value']
            route_info['traffic_delay_minutes'] = route_info['traffic_delay_seconds'] / 60
        
        route_analysis.append(route_info)
        
        # Print route details
        print(f"\n🚗 Route {i+1}: {route_info['summary']}")
        print(f"   Distance: {route_info['distance_text']} ({route_info['distance_meters']:,} meters)")
        print(f"   Duration (no traffic): {route_info['duration_text']} ({route_info['duration_seconds']} seconds)")
        
        if 'traffic_duration_seconds' in route_info:
            print(f"   Duration (with traffic): {route_info['traffic_duration_text']} ({route_info['traffic_duration_seconds']} seconds)")
            print(f"   Traffic delay: {route_info['traffic_delay_minutes']:.1f} minutes")
            
            # Calculate traffic impact
            if route_info['traffic_delay_seconds'] > 0:
                impact_pct = (route_info['traffic_delay_seconds'] / route_info['duration_seconds']) * 100
                print(f"   Traffic impact: +{impact_pct:.1f}% longer due to traffic")
            else:
                print(f"   Traffic impact: No significant delay")
        
        # Analyze steps for this route
        if 'steps' in leg:
            total_steps = len(leg['steps'])
            print(f"   Route segments: {total_steps} steps")
            
            # Show key segments
            major_steps = [step for step in leg['steps'] if step['distance']['value'] > 100]  # Steps > 100m
            if major_steps:
                print(f"   Major segments ({len(major_steps)}):")
                for j, step in enumerate(major_steps[:3]):  # Show top 3 segments
                    instruction = step['html_instructions'].replace('<b>', '').replace('</b>', '').replace('<div style="font-size:0.9em">', ' - ').replace('</div>', '')
                    print(f"     {j+1}. {instruction[:80]}{'...' if len(instruction) > 80 else ''}")
                    print(f"        Distance: {step['distance']['text']}, Duration: {step['duration']['text']}")

    # Create comparison summary
    if len(route_analysis) > 1:
        print(f"\n📊 Route Comparison Summary:")
        print("=" * 50)
        
        # Find fastest route
        if all('traffic_duration_seconds' in r for r in route_analysis):
            fastest = min(route_analysis, key=lambda x: x['traffic_duration_seconds'])
            print(f"🏆 Fastest route (with traffic): Route {fastest['route_number']}")
            print(f"   Duration: {fastest['traffic_duration_text']}")
        else:
            fastest = min(route_analysis, key=lambda x: x['duration_seconds'])
            print(f"🏆 Fastest route: Route {fastest['route_number']}")
            print(f"   Duration: {fastest['duration_text']}")
        
        # Find shortest route
        shortest = min(route_analysis, key=lambda x: x['distance_meters'])
        print(f"📏 Shortest route: Route {shortest['route_number']}")
        print(f"   Distance: {shortest['distance_text']}")
        
        # Traffic impact comparison
        if all('traffic_delay_seconds' in r for r in route_analysis):
            most_affected = max(route_analysis, key=lambda x: x['traffic_delay_seconds'])
            least_affected = min(route_analysis, key=lambda x: x['traffic_delay_seconds'])
            
            print(f"🚦 Most affected by traffic: Route {most_affected['route_number']} (+{most_affected['traffic_delay_minutes']:.1f} min)")
            print(f"✅ Least affected by traffic: Route {least_affected['route_number']} (+{least_affected['traffic_delay_minutes']:.1f} min)")

else:
    print("❌ No driving route data available for analysis")


Analyzing route segments and traffic data...

🔍 Detailed Route Analysis:

🚗 Route 1: The Chase
   Distance: 2.0 km (2,004 meters)
   Duration (no traffic): 5 mins (291 seconds)
   Duration (with traffic): 5 mins (314 seconds)
   Traffic delay: 0.4 minutes
   Traffic impact: +7.9% longer due to traffic
   Route segments: 9 steps
   Major segments (6):
     1. Head northeast on Perimeter Rd
        Distance: 0.1 km, Duration: 1 min
     2. At the roundabout, take the 4th exit and stay on Perimeter Rd
        Distance: 0.2 km, Duration: 1 min
     3. At Cathedral Roundabout, take the 1st exit onto The Chase
        Distance: 0.7 km, Duration: 1 min

🚗 Route 2: The Chase and Farnham Rd/A31
   Distance: 2.1 km (2,131 meters)
   Duration (no traffic): 5 mins (317 seconds)
   Duration (with traffic): 5 mins (320 seconds)
   Traffic delay: 0.1 minutes
   Traffic impact: +0.9% longer due to traffic
   Route segments: 9 steps
   Major segments (6):
     1. Head northeast on Perimeter Rd
        

### 5.6 Bonus: Distance Matrix for Multiple Origins/Destinations


In [64]:
# Use Google Maps Distance Matrix API for multiple origins/destinations
print("Getting distance matrix for multiple locations...")

# Define multiple origins and destinations in the Guildford area
origins = [
    "University of Surrey, Guildford, UK",
    "Guildford Castle, Guildford, UK",
    "Guildford Cathedral, Guildford, UK"
]

destinations = [
    "Guildford Railway Station, Guildford, UK",
    "Guildford High Street, Guildford, UK",
    "Royal Surrey County Hospital, Guildford, UK"
]

try:
    # Get distance matrix with traffic
    matrix_result = gmaps.distance_matrix(
        origins=origins,
        destinations=destinations,
        mode="driving",
        departure_time=departure_time,
        traffic_model="best_guess"
    )
    
    if matrix_result['status'] == 'OK':
        print("✅ Distance matrix retrieved successfully!")
        
        # Create a formatted table
        print(f"\n📊 Distance Matrix (Driving with Traffic):")
        print("=" * 100)
        
        # Print header
        header = "Origin".ljust(25) + " | "
        for dest in destinations:
            dest_short = dest.split(',')[0][:20]  # Shorten destination names
            header += dest_short.ljust(22) + " | "
        print(header)
        print("-" * 100)
        
        # Print matrix data
        for i, origin in enumerate(origins):
            origin_short = origin.split(',')[0][:24]  # Shorten origin name
            row = origin_short.ljust(25) + " | "
            
            for j, dest in enumerate(destinations):
                element = matrix_result['rows'][i]['elements'][j]
                
                if element['status'] == 'OK':
                    distance = element['distance']['text']
                    
                    # Use traffic duration if available, otherwise regular duration
                    if 'duration_in_traffic' in element:
                        duration = element['duration_in_traffic']['text']
                    else:
                        duration = element['duration']['text']
                    
                    cell_text = f"{distance} / {duration}"
                else:
                    cell_text = "No route"
                
                row += cell_text.ljust(22) + " | "
            
            print(row)
        
        print("\nFormat: Distance / Duration (with traffic)")
        
        # Find shortest and fastest routes in matrix
        print(f"\n🎯 Matrix Analysis:")
        min_distance_val = float('inf')
        min_duration_val = float('inf')
        min_distance_route = None
        min_duration_route = None
        
        for i, origin in enumerate(origins):
            for j, dest in enumerate(destinations):
                element = matrix_result['rows'][i]['elements'][j]
                
                if element['status'] == 'OK':
                    distance_val = element['distance']['value']
                    
                    # Use traffic duration if available
                    if 'duration_in_traffic' in element:
                        duration_val = element['duration_in_traffic']['value']
                    else:
                        duration_val = element['duration']['value']
                    
                    if distance_val < min_distance_val:
                        min_distance_val = distance_val
                        min_distance_route = (origins[i].split(',')[0], destinations[j].split(',')[0], element['distance']['text'])
                    
                    if duration_val < min_duration_val:
                        min_duration_val = duration_val
                        if 'duration_in_traffic' in element:
                            duration_text = element['duration_in_traffic']['text']
                        else:
                            duration_text = element['duration']['text']
                        min_duration_route = (origins[i].split(',')[0], destinations[j].split(',')[0], duration_text)
        
        if min_distance_route:
            print(f"📏 Shortest route: {min_distance_route[0]} → {min_distance_route[1]} ({min_distance_route[2]})")
        
        if min_duration_route:
            print(f"⚡ Fastest route: {min_duration_route[0]} → {min_duration_route[1]} ({min_duration_route[2]})")
    
    else:
        print(f"❌ Distance matrix request failed: {matrix_result['status']}")
        
except Exception as e:
    print(f"Error getting distance matrix: {e}")


Getting distance matrix for multiple locations...
✅ Distance matrix retrieved successfully!

📊 Distance Matrix (Driving with Traffic):
Origin                    | Guildford Railway St   | Guildford High Stree   | Royal Surrey County    | 
----------------------------------------------------------------------------------------------------
University of Surrey      | 2.0 km / 5 mins        | 2.3 km / 6 mins        | 1.4 km / 3 mins        | 
Guildford Castle          | 1.5 km / 7 mins        | 1.8 km / 8 mins        | 3.9 km / 11 mins       | 
Guildford Cathedral       | 2.0 km / 6 mins        | 2.3 km / 7 mins        | 1.3 km / 4 mins        | 

Format: Distance / Duration (with traffic)

🎯 Matrix Analysis:
📏 Shortest route: Guildford Cathedral → Royal Surrey County Hospital (1.3 km)
⚡ Fastest route: University of Surrey → Royal Surrey County Hospital (3 mins)


In [65]:
# Summary of Google Maps routing analysis
print("\n" + "="*80)
print("🎯 GOOGLE MAPS ROUTING ANALYSIS SUMMARY")
print("="*80)

if walking_result and driving_result:
    # Walking vs Driving comparison
    walking_leg = walking_result[0]['legs'][0]
    driving_leg = driving_result[0]['legs'][0]  # Best route
    
    print(f"\n🚶 Walking Route:")
    print(f"   Distance: {walking_leg['distance']['text']}")
    print(f"   Duration: {walking_leg['duration']['text']}")
    
    print(f"\n🚗 Driving Route (Best):")
    print(f"   Distance: {driving_leg['distance']['text']}")
    print(f"   Duration: {driving_leg['duration']['text']}")
    if 'duration_in_traffic' in driving_leg:
        print(f"   Duration with traffic: {driving_leg['duration_in_traffic']['text']}")
        
        # Calculate time savings
        walking_seconds = walking_leg['duration']['value']
        driving_seconds = driving_leg['duration_in_traffic']['value']
        time_saved = walking_seconds - driving_seconds
        
        if time_saved > 0:
            print(f"   Time saved vs walking: {time_saved//60} min {time_saved%60} sec")
            print(f"   Speed advantage: {time_saved/walking_seconds*100:.1f}% faster")
        else:
            print(f"   Note: Driving takes longer due to traffic/routing")

    # Traffic impact analysis
    if traffic_results:
        print(f"\n🚦 Traffic Impact Analysis:")
        for model, result in traffic_results.items():
            if result:
                leg = result[0]['legs'][0]
                if 'duration_in_traffic' in leg:
                    base_duration = leg['duration']['value']
                    traffic_duration = leg['duration_in_traffic']['value']
                    delay = traffic_duration - base_duration
                    
                    print(f"   {model.title()}: +{delay//60}min {delay%60}sec delay ({delay/base_duration*100:.1f}% increase)")

    # Alternative routes summary
    if len(driving_result) > 1:
        print(f"\n🛣️  Alternative Routes Available: {len(driving_result)} options")
        for i, route in enumerate(driving_result[:3]):  # Show top 3
            leg = route['legs'][0]
            summary = route.get('summary', f'Route {i+1}')
            if 'duration_in_traffic' in leg:
                duration = leg['duration_in_traffic']['text']
            else:
                duration = leg['duration']['text']
            print(f"   Route {i+1}: {summary} - {leg['distance']['text']}, {duration}")

print(f"\n✅ Google Maps routing analysis complete!")
print(f"📍 Route: University of Surrey → Guildford Railway Station")
print(f"🕒 Analysis time: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}")
print("="*80)



🎯 GOOGLE MAPS ROUTING ANALYSIS SUMMARY

🚶 Walking Route:
   Distance: 0.8 km
   Duration: 11 mins

🚗 Driving Route (Best):
   Distance: 2.0 km
   Duration: 5 mins
   Duration with traffic: 5 mins
   Time saved vs walking: 6 min 12 sec
   Speed advantage: 54.2% faster

🚦 Traffic Impact Analysis:
   Best_Guess: +0min 23sec delay (7.9% increase)
   Pessimistic: +2min 24sec delay (49.5% increase)
   Optimistic: +-1min 35sec delay (-8.6% increase)

🛣️  Alternative Routes Available: 3 options
   Route 1: The Chase - 2.0 km, 5 mins
   Route 2: The Chase and Farnham Rd/A31 - 2.1 km, 5 mins
   Route 3: The Chase and Wodeland Ave - 2.5 km, 7 mins

✅ Google Maps routing analysis complete!
📍 Route: University of Surrey → Guildford Railway Station
🕒 Analysis time: 2025-09-19 12:39:18
